## Planning the Project and Further Preparing the UFC Data: 

In [60]:
# imports

import pandas as pd
import numpy as np

# Ignore Warnings
import warnings
warnings.filterwarnings("ignore")

from Wrangle_UFC import *

In [2]:
# Remove Limits On Viewing Dataframes
pd.set_option('display.max_columns', None)

In [3]:
ufc_cleaned = get_n_prep_ufc()

In [4]:
ufc_cleaned.head()

event_name         fighter       opponent  \
0           UFC 259: Blachowicz vs. Adesanya      Aalon Cruz     Uros Medic   
1  UFC Fight Night: Benavidez vs. Figueiredo      Aalon Cruz  Spike Carlyle   
3    UFC Fight Night: Henderson vs Dos Anjos  Aaron Phillips     Matt Hobar   
4            UFC Fight Night: Kattar vs. Ige  Aaron Phillips     Jack Shore   
5                UFC 173: Barao vs Dillashaw  Aaron Phillips    Sam Sicilia   

   w  l  d  nc  total_rounds  belt  womens_bout  interim_bout  strawweight  \
0  0  1  0   0             3     0            0             0            0   
1  0  1  0   0             3     0            0             0            0   
3  0  1  0   0             3     0            0             0            0   
4  0  1  0   0             3     0            0             0            0   
5  0  1  0   0             3     0            0             0            0   

   flyweight  bantamweight  featherweight  lightweight  middleweight  \
0          0             0              0            1             0   
1          0             0              1            0             0   
3          0             1              0            0             0   
4          0             1              0            0             0   
5          0             0              1            0             0   

   light_heavyweight  heavyweight  catch_weight  open_weight  \
0                  0            0             0            0   
1                  0            0             0            0   
3                  0            0             0            0   
4                  0            0             0            0   
5                  0            0             0            0   

   super_heavyweight  superfight fight_city fight_state         fight_country  \
0                  0           0  Las Vegas      Nevada                   USA   
1                  0           0    Norfolk    Virginia                   USA   
3                  0           0      Tulsa    Oklahoma                   USA   
4                  0           0  Abu Dhabi   Abu Dhabi  United Arab Emirates   
5                  0           0  Las Vegas      Nevada                   USA   

   weight  reach    stance  slpm  stracc  sapm  strdef  tdavg  tdacc  tddef  \
0   145.0   78.0    Switch  7.58      39  8.88      58    0.0      0      0   
1   145.0   78.0    Switch  7.58      39  8.88      58    0.0      0      0   
3   135.0   71.0  Southpaw  1.65      56  3.44      39    0.0      0     44   
4   135.0   71.0  Southpaw  1.65      56  3.44      39    0.0      0     44   
5   135.0   71.0  Southpaw  1.65      56  3.44      39    0.0      0     44   

   subavg  age_days   age outcome  height_in  stance_Orthodox  \
0     0.0     11490  31.0    loss         72                0   
1     0.0     11119  30.0    loss         72                0   
3     0.4      9149  25.0    loss         69                0   
4     0.4     11302  30.0    loss         69                0   
5     0.4      9058  24.0    loss         69                0   

   stance_Southpaw  stance_Switch  
0                0              1  
1                0              1  
3                1              0  
4                1              0  
5                1              0

In [5]:
ufc_cleaned.columns

Index(['event_name', 'fighter', 'opponent', 'w', 'l', 'd', 'nc',
       'total_rounds', 'belt', 'womens_bout', 'interim_bout', 'strawweight',
       'flyweight', 'bantamweight', 'featherweight', 'lightweight',
       'middleweight', 'light_heavyweight', 'heavyweight', 'catch_weight',
       'open_weight', 'super_heavyweight', 'superfight', 'fight_city',
       'fight_state', 'fight_country', 'weight', 'reach', 'stance', 'slpm',
       'stracc', 'sapm', 'strdef', 'tdavg', 'tdacc', 'tddef', 'subavg',
       'age_days', 'age', 'outcome', 'height_in', 'stance_Orthodox',
       'stance_Southpaw', 'stance_Switch'],
      dtype='object')

### Plan and Scope

I want to create a df for the bouts only that lists : 'event_name', 'fighter', 'opponent', 'w', 'l', 'd', 'nc',
       'total_rounds', 'belt', 'womens_bout', 'interim_bout', 'strawweight',
       'flyweight', 'bantamweight', 'featherweight', 'lightweight',
       'middleweight', 'light_heavyweight', 'heavyweight', 'catch_weight',
       'open_weight', 'super_heavyweight', 'superfight', 'fight_city',
       'fight_state', 'fight_country', 'outcome'

I also want to create a df for the first fighter with all of their stats. 

I want to create another df for the second fighter will all of their stats. 

I want to merge all three df together. 

Split and explore. 

To model this is what I'm thinking: 

If I find the differences in stats between the two fighters and assign it to just one fighter like: fighter1 +23 average strikes, fighter1 -2 average takedown defense, etc. Then the target will be outcome (fighter1 or fighter2). It will then associate positive averages with fighter1 and negative averages with fighter2 winning. 

### Create Bouts DF

In [6]:
# add the columns I would like to work with into a new df
bouts = ufc_cleaned[['event_name', 'fighter', 'opponent', 'w', 'l', 'd', 'nc', 'total_rounds', 'belt', 'womens_bout', 'interim_bout', 'strawweight', 'flyweight', 'bantamweight', 'featherweight', 'lightweight', 'middleweight', 'light_heavyweight', 'heavyweight', 'catch_weight', 'open_weight', 'super_heavyweight', 'superfight', 'fight_city', 'fight_state', 'fight_country', 'outcome']].copy(0)

In [7]:
bouts.head(1)

event_name     fighter    opponent  w  l  d  nc  \
0  UFC 259: Blachowicz vs. Adesanya  Aalon Cruz  Uros Medic  0  1  0   0   

   total_rounds  belt  womens_bout  interim_bout  strawweight  flyweight  \
0             3     0            0             0            0          0   

   bantamweight  featherweight  lightweight  middleweight  light_heavyweight  \
0             0              0            1             0                  0   

   heavyweight  catch_weight  open_weight  super_heavyweight  superfight  \
0            0             0            0                  0           0   

  fight_city fight_state fight_country outcome  
0  Las Vegas      Nevada           USA    loss

In [11]:
fighter_stats = ufc_cleaned[['fighter', 'opponent', 'weight', 'reach', 'stance', 'slpm',
       'stracc', 'sapm', 'strdef', 'tdavg', 'tdacc', 'tddef', 'subavg',
       'age_days', 'age', 'outcome', 'height_in', 'stance_Orthodox',
       'stance_Southpaw', 'stance_Switch']].copy(0)

In [12]:
fighter_stats.head()

fighter       opponent  weight  reach    stance  slpm  stracc  sapm  \
0      Aalon Cruz     Uros Medic   145.0   78.0    Switch  7.58      39  8.88   
1      Aalon Cruz  Spike Carlyle   145.0   78.0    Switch  7.58      39  8.88   
3  Aaron Phillips     Matt Hobar   135.0   71.0  Southpaw  1.65      56  3.44   
4  Aaron Phillips     Jack Shore   135.0   71.0  Southpaw  1.65      56  3.44   
5  Aaron Phillips    Sam Sicilia   135.0   71.0  Southpaw  1.65      56  3.44   

   strdef  tdavg  tdacc  tddef  subavg  age_days   age outcome  height_in  \
0      58    0.0      0      0     0.0     11490  31.0    loss         72   
1      58    0.0      0      0     0.0     11119  30.0    loss         72   
3      39    0.0      0     44     0.4      9149  25.0    loss         69   
4      39    0.0      0     44     0.4     11302  30.0    loss         69   
5      39    0.0      0     44     0.4      9058  24.0    loss         69   

   stance_Orthodox  stance_Southpaw  stance_Switch  
0                0                0              1  
1                0                0              1  
3                0                1              0  
4                0                1              0  
5                0                1              0

In [26]:
fighter_stats.reset_index(drop = True, inplace = True)

In [27]:
fighter_stats['concat'] = fighter_stats.fighter + fighter_stats.opponent
fighter_stats['reverse'] = fighter_stats.opponent + fighter_stats.fighter

In [28]:
fighter_stats.head()

fighter       opponent  weight  reach    stance  slpm  stracc  sapm  \
0      Aalon Cruz     Uros Medic   145.0   78.0    Switch  7.58      39  8.88   
1      Aalon Cruz  Spike Carlyle   145.0   78.0    Switch  7.58      39  8.88   
2  Aaron Phillips     Matt Hobar   135.0   71.0  Southpaw  1.65      56  3.44   
3  Aaron Phillips     Jack Shore   135.0   71.0  Southpaw  1.65      56  3.44   
4  Aaron Phillips    Sam Sicilia   135.0   71.0  Southpaw  1.65      56  3.44   

   strdef  tdavg  tdacc  tddef  subavg  age_days   age outcome  height_in  \
0      58    0.0      0      0     0.0     11490  31.0    loss         72   
1      58    0.0      0      0     0.0     11119  30.0    loss         72   
2      39    0.0      0     44     0.4      9149  25.0    loss         69   
3      39    0.0      0     44     0.4     11302  30.0    loss         69   
4      39    0.0      0     44     0.4      9058  24.0    loss         69   

   stance_Orthodox  stance_Southpaw  stance_Switch                     concat  \
0                0                0              1       Aalon CruzUros Medic   
1                0                0              1    Aalon CruzSpike Carlyle   
2                0                1              0   Aaron PhillipsMatt Hobar   
3                0                1              0   Aaron PhillipsJack Shore   
4                0                1              0  Aaron PhillipsSam Sicilia   

                     reverse  
0       Uros MedicAalon Cruz  
1    Spike CarlyleAalon Cruz  
2   Matt HobarAaron Phillips  
3   Jack ShoreAaron Phillips  
4  Sam SiciliaAaron Phillips

In [29]:
fighter_stats.shape

(10840, 22)

In [30]:
line0concat = fighter_stats.iloc[0].concat

In [31]:
line0reverse = fighter_stats.iloc[0].reverse

In [43]:
fighter_stats[(fighter_stats.concat == line0reverse) & (fighter_stats.reverse == line0concat)].index

Int64Index([10360], dtype='int64')

In [40]:
columns = ['fighter1', 'fighter2', 'weight_f1', 'reach_f1', 'stance_f1', 'slpm_f1',
       'stracc_f1', 'sapm_f1', 'strdef_f1', 'tdavg_f1', 'tdacc_f1', 'tddef_f1', 'subavg_f1',
       'age_days_f1', 'age_f1', 'outcome_f1', 'height_in_f1', 'stance_Orthodox_f1',
       'stance_Southpaw_f1', 'stance_Switch_f1', 'concat', 'reverse', 'fighter1', 'fighter2', 'weight_f2', 'reach_f2', 'stance_f2', 'slpm_f2',
       'stracc_f2', 'sapm_f2', 'strdef_f2', 'tdavg_f2', 'tdacc_f2', 'tddef_f2', 'subavg_f2',
       'age_days_f2', 'age_f2', 'outcome_f2', 'height_in_f2', 'stance_Orthodox_f2',
       'stance_Southpaw_f2', 'stance_Switch_f2', 'concat2', 'reverse2']

In [41]:
final_df = pd.DataFrame(columns = columns)

In [42]:
final_df.head()

Empty DataFrame
Columns: [fighter1, fighter2, weight_f1, reach_f1, stance_f1, slpm_f1, stracc_f1, sapm_f1, strdef_f1, tdavg_f1, tdacc_f1, tddef_f1, subavg_f1, age_days_f1, age_f1, outcome_f1, height_in_f1, stance_Orthodox_f1, stance_Southpaw_f1, stance_Switch_f1, concat, reverse, fighter1, fighter2, weight_f2, reach_f2, stance_f2, slpm_f2, stracc_f2, sapm_f2, strdef_f2, tdavg_f2, tdacc_f2, tddef_f2, subavg_f2, age_days_f2, age_f2, outcome_f2, height_in_f2, stance_Orthodox_f2, stance_Southpaw_f2, stance_Switch_f2, concat2, reverse2]
Index: []

In [55]:
for i in range(len (fighter_stats)):
    lineconcat = fighter_stats.iloc[i].concat
    linereverse = fighter_stats.iloc[i].reverse
    
    arrayf1 = fighter_stats.iloc[i].values
    print (arrayf1)
    arrayf2_index = list(fighter_stats[(fighter_stats.concat == linereverse) & (fighter_stats.reverse == lineconcat)].index)
    print (arrayf2_index)
    
    if len(arrayf2_index) == 0:
        continue
    elif len(arrayf2_index) > 1:
        continue 
    
    arrayf2 = fighter_stats.iloc[arrayf2_index].values[0]
    print (arrayf2)
    
    joined = np.concatenate((arrayf1, arrayf2))
    
    final_df.loc[len(final_df.index)] = joined
    
    
    

['Aalon Cruz' 'Uros Medic' 145.0 78.0 'Switch' 7.58 39 8.88 58 0.0 0 0 0.0
 11490 31.0 'loss' 72 0 0 1 'Aalon CruzUros Medic' 'Uros MedicAalon Cruz']
[10360]
['Uros Medic' 'Aalon Cruz' 155.0 71.0 'Southpaw' 19.91 77 0.52 86 0.0 0
 100 0.0 10177 27.0 'win' 73 0 1 0 'Uros MedicAalon Cruz'
 'Aalon CruzUros Medic']
['Aalon Cruz' 'Spike Carlyle' 145.0 78.0 'Switch' 7.58 39 8.88 58 0.0 0 0
 0.0 11119 30.0 'loss' 72 0 0 1 'Aalon CruzSpike Carlyle'
 'Spike CarlyleAalon Cruz']
[9578]
['Spike Carlyle' 'Aalon Cruz' 145.0 71.0 'Switch' 2.55 54 3.85 30 3.34 36
 57 0.5 9795 26.0 'win' 68 0 0 1 'Spike CarlyleAalon Cruz'
 'Aalon CruzSpike Carlyle']
['Aaron Phillips' 'Matt Hobar' 135.0 71.0 'Southpaw' 1.65 56 3.44 39 0.0 0
 44 0.4 9149 25.0 'loss' 69 0 1 0 'Aaron PhillipsMatt Hobar'
 'Matt HobarAaron Phillips']
[7008]
['Matt Hobar' 'Aaron Phillips' 135.0 70.0 'Southpaw' 3.23 42 4.27 52 3.66
 44 50 0.0 10090 27.0 'win' 70 0 1 0 'Matt HobarAaron Phillips'
 'Aaron PhillipsMatt Hobar']
['Aaron Phillips' 'J

['Abubakar Nurmagomedov' 'Jared Gooden' 170.0 72.0 'Orthodox' 3.59 49 2.52
 69 1.68 33 0 0.0 11457 31.0 'win' 71 1 0 0
 'Abubakar NurmagomedovJared Gooden' 'Jared GoodenAbubakar Nurmagomedov']
[4566]
['Jared Gooden' 'Abubakar Nurmagomedov' 170.0 77.0 'Orthodox' 4.77 41 7.6
 49 0.5 100 83 0.0 9974 27.0 'loss' 72 1 0 0
 'Jared GoodenAbubakar Nurmagomedov' 'Abubakar NurmagomedovJared Gooden']
['Abubakar Nurmagomedov' 'David Zawada' 170.0 72.0 'Orthodox' 3.59 49 2.52
 69 1.68 33 0 0.0 10953 30.0 'loss' 71 1 0 0
 'Abubakar NurmagomedovDavid Zawada' 'David ZawadaAbubakar Nurmagomedov']
[2598]
['David Zawada' 'Abubakar Nurmagomedov' 170.0 75.0 'Orthodox' 3.24 40 4.07
 54 0.96 30 57 2.2 10692 29.0 'win' 72 1 0 0
 'David ZawadaAbubakar Nurmagomedov' 'Abubakar NurmagomedovDavid Zawada']
['Adam Milstead' 'Curtis Blaydes' 205.0 76.0 'Orthodox' 3.85 46 4.79 43
 0.0 0 64 0.0 10809 29.0 'no_contest' 75 1 0 0
 'Adam MilsteadCurtis Blaydes' 'Curtis BlaydesAdam Milstead']
[2182]
['Curtis Blaydes' 'Adam 

 'Dan HookerAl Iaquinta']
[2301]
['Dan Hooker' 'Al Iaquinta' 155.0 75.0 'Switch' 4.95 48 4.92 51 0.72 34 79
 0.3 10826 29.0 'win' 72 0 0 1 'Dan HookerAl Iaquinta'
 'Al IaquintaDan Hooker']
['Al Iaquinta' 'Joe Lauzon' 155.0 70.0 'Orthodox' 4.06 40 4.44 61 0.64 18
 74 0.2 10138 27.0 'win' 70 1 0 0 'Al IaquintaJoe Lauzon'
 'Joe LauzonAl Iaquinta']
[5021]
['Joe Lauzon' 'Al Iaquinta' 155.0 71.0 'Orthodox' 2.84 39 5.39 54 2.39 45
 54 2.0 11211 30.0 'loss' 70 1 0 0 'Joe LauzonAl Iaquinta'
 'Al IaquintaJoe Lauzon']
['Al Iaquinta' 'Khabib Nurmagomedov' 155.0 70.0 'Orthodox' 4.06 40 4.44 61
 0.64 18 74 0.2 11300 30.0 'loss' 70 1 0 0
 'Al IaquintaKhabib Nurmagomedov' 'Khabib NurmagomedovAl Iaquinta']
[6047]
['Khabib Nurmagomedov' 'Al Iaquinta' 155.0 70.0 'Orthodox' 4.1 48 1.75 65
 5.32 48 84 0.8 10791 29.0 'win' 70 1 0 0 'Khabib NurmagomedovAl Iaquinta'
 'Al IaquintaKhabib Nurmagomedov']
['Al Iaquinta' 'Piotr Hallmann' 155.0 70.0 'Orthodox' 4.06 40 4.44 61 0.64
 18 74 0.2 9676 26.0 'win' 70 1 0 0

['Alan Patrick' 'John Makdessi' 155.0 74.0 'Southpaw' 1.79 40 2.64 43 3.48
 38 50 0.3 11155 30.0 'win' 71 0 1 0 'Alan PatrickJohn Makdessi'
 'John MakdessiAlan Patrick']
[5204]
['John Makdessi' 'Alan Patrick' 155.0 68.0 'Orthodox' 5.57 51 4.02 69 0.0
 0 89 0.0 10501 28.0 'loss' 68 1 0 0 'John MakdessiAlan Patrick'
 'Alan PatrickJohn Makdessi']
['Albert Morales' 'Andre Soukhamthath' 135.0 72.0 'Orthodox' 3.81 35 3.96
 56 0.91 35 70 0.2 9415 25.0 'win' 69 1 0 0
 'Albert MoralesAndre Soukhamthath' 'Andre SoukhamthathAlbert Morales']
[576]
['Andre Soukhamthath' 'Albert Morales' 135.0 70.0 'Orthodox' 2.77 44 4.31
 49 1.25 53 58 0.2 10359 28.0 'loss' 69 1 0 0
 'Andre SoukhamthathAlbert Morales' 'Albert MoralesAndre Soukhamthath']
['Albert Morales' 'Thomas Almeida' 135.0 72.0 'Orthodox' 3.81 35 3.96 56
 0.91 35 70 0.2 9310 25.0 'loss' 69 1 0 0 'Albert MoralesThomas Almeida'
 'Thomas AlmeidaAlbert Morales']
[9963]
['Thomas Almeida' 'Albert Morales' 145.0 70.0 'Southpaw' 4.84 43 4.93 61
 0.17 1

['Aleksei Kunchenko' 'Elizeu Zaleski dos Santos' 170.0 70.0 'Orthodox'
 3.67 44 2.83 63 0.25 33 80 0.0 13100 35.0 'loss' 68 1 0 0
 'Aleksei KunchenkoElizeu Zaleski dos Santos'
 'Elizeu Zaleski dos SantosAleksei Kunchenko']
[3260]
['Elizeu Zaleski dos Santos' 'Aleksei Kunchenko' 170.0 73.0 'Orthodox'
 4.05 39 3.07 59 0.57 17 52 0.5 12147 33.0 'win' 71 1 0 0
 'Elizeu Zaleski dos SantosAleksei Kunchenko'
 'Aleksei KunchenkoElizeu Zaleski dos Santos']
['Aleksei Kunchenko' 'Thiago Alves' 170.0 70.0 'Orthodox' 3.67 44 2.83 63
 0.25 33 80 0.0 12554 34.0 'win' 68 1 0 0 'Aleksei KunchenkoThiago Alves'
 'Thiago AlvesAleksei Kunchenko']
[9881]
['Thiago Alves' 'Aleksei Kunchenko' 170.0 70.0 'Orthodox' 3.73 41 3.42 62
 0.71 60 63 0.3 12766 34.0 'loss' 69 1 0 0 'Thiago AlvesAleksei Kunchenko'
 'Aleksei KunchenkoThiago Alves']
['Aleksei Kunchenko' 'Yushin Okami' 170.0 70.0 'Orthodox' 3.67 44 2.83 63
 0.25 33 80 0.0 12631 34.0 'win' 68 1 0 0 'Aleksei KunchenkoYushin Okami'
 'Yushin OkamiAleksei Kunche

...

['Yoshihiro Akiyama' 'Alan Belcher' 170.0 75.0 'Orthodox' 3.1 41 3.62 57
 2.29 67 92 1.0 12401 33.0 'win' 70 1 0 0 'Yoshihiro AkiyamaAlan Belcher'
 'Alan BelcherYoshihiro Akiyama']
[105]
['Alan Belcher' 'Yoshihiro Akiyama' 185.0 75.0 'Orthodox' 2.7 41 3.1 59
 0.44 26 55 0.9 9209 25.0 'loss' 74 1 0 0 'Alan BelcherYoshihiro Akiyama'
 'Yoshihiro AkiyamaAlan Belcher']
['Yoshihiro Akiyama' 'Chris Leben' 170.0 75.0 'Orthodox' 3.1 41 3.62 57
 2.29 67 92 1.0 12758 34.0 'loss' 70 1 0 0 'Yoshihiro AkiyamaChris Leben'
 'Chris LebenYoshihiro Akiyama']
[1776]
['Chris Leben' 'Yoshihiro Akiyama' 185.0 73.0 'Southpaw' 2.87 42 2.87 52
 1.14 41 53 0.8 10939 29.0 'win' 71 0 1 0 'Chris LebenYoshihiro Akiyama'
 'Yoshihiro AkiyamaChris Leben']
['Yoshihiro Akiyama' 'Amir Sadollah' 170.0 75.0 'Orthodox' 3.1 41 3.62 57
 2.29 67 92 1.0 14298 39.0 'win' 70 1 0 0 'Yoshihiro AkiyamaAmir Sadollah'
 'Amir SadollahYoshihiro Akiyama']
[514]
['Amir Sadollah' 'Yoshihiro Akiyama' 170.0 75.0 'Orthodox' 4.71 46 3.55 60
 0.

['Yushin Okami' 'Jacare Souza' 170.0 75.0 'Southpaw' 2.06 38 2.25 60 1.98
 39 84 0.5 11733 32.0 'loss' 74 0 1 0 'Yushin OkamiJacare Souza'
 'Jacare SouzaYushin Okami']
[4333]
['Jacare Souza' 'Yushin Okami' 185.0 72.0 'Orthodox' 2.53 47 2.83 62 2.57
 39 57 1.3 12325 33.0 'win' 73 1 0 0 'Jacare SouzaYushin Okami'
 'Yushin OkamiJacare Souza']
['Yushin Okami' 'Mike Swick' 170.0 75.0 'Southpaw' 2.06 38 2.25 60 1.98 39
 84 0.5 9391 25.0 'win' 74 0 1 0 'Yushin OkamiMike Swick'
 'Mike SwickYushin Okami']
[7532]
['Mike Swick' 'Yushin Okami' 170.0 77.0 'Orthodox' 2.36 37 2.29 54 1.06 50
 61 0.6 10154 27.0 'loss' 73 1 0 0 'Mike SwickYushin Okami'
 'Yushin OkamiMike Swick']
['Yushin Okami' 'Alan Belcher' 170.0 75.0 'Southpaw' 2.06 38 2.25 60 1.98
 39 84 0.5 11484 31.0 'win' 74 0 1 0 'Yushin OkamiAlan Belcher'
 'Alan BelcherYushin Okami']
[116, 119]
['Yushin Okami' 'Aleksei Kunchenko' 170.0 75.0 'Southpaw' 2.06 38 2.25 60
 1.98 39 84 0.5 13647 37.0 'loss' 74 0 1 0 'Yushin OkamiAleksei Kunchenko'
 '

['Yves Edwards' 'Jeremy Stephens' 155.0 73.0 'Southpaw' 2.91 42 2.34 66
 0.76 53 69 0.7 13218 36.0 'win' 69 0 1 0 'Yves EdwardsJeremy Stephens'
 'Jeremy StephensYves Edwards']
[4763]
['Jeremy Stephens' 'Yves Edwards' 145.0 71.0 'Orthodox' 3.18 40 3.06 58
 1.16 38 65 0.4 9694 26.0 'loss' 69 1 0 0 'Jeremy StephensYves Edwards'
 'Yves EdwardsJeremy Stephens']
['Yves Edwards' 'Nick Agallar' 155.0 73.0 'Southpaw' 2.91 42 2.34 66 0.76
 53 69 0.7 9913 27.0 'win' 69 0 1 0 'Yves EdwardsNick Agallar'
 'Nick AgallarYves Edwards']
[]
['Yves Edwards' 'Hermes Franca' 155.0 73.0 'Southpaw' 2.91 42 2.34 66 0.76
 53 69 0.7 10046 27.0 'win' 69 0 1 0 'Yves EdwardsHermes Franca'
 'Hermes FrancaYves Edwards']
[4132]
['Hermes Franca' 'Yves Edwards' 155.0 71.0 'Orthodox' 1.78 39 2.85 55 1.53
 36 37 2.4 10812 29.0 'loss' 66 1 0 0 'Hermes FrancaYves Edwards'
 'Yves EdwardsHermes Franca']
['Yves Edwards' 'Joe Stevenson' 155.0 73.0 'Southpaw' 2.91 42 2.34 66 0.76
 53 69 0.7 10873 29.0 'loss' 69 0 1 0 'Yves Edwar

['Zak Cummings' 'Trevin Giles' 185.0 75.0 'Southpaw' 2.58 32 2.83 55 0.68
 28 65 0.7 12707 34.0 'win' 72 0 1 0 'Zak CummingsTrevin Giles'
 'Trevin GilesZak Cummings']
[10258]
['Trevin Giles' 'Zak Cummings' 185.0 74.0 'Orthodox' 3.26 56 1.88 62 1.37
 80 79 0.3 9781 26.0 'loss' 72 1 0 0 'Trevin GilesZak Cummings'
 'Zak CummingsTrevin Giles']
['Zak Cummings' 'Trevor Smith' 185.0 75.0 'Southpaw' 2.58 32 2.83 55 0.68
 28 65 0.7 12553 34.0 'win' 72 0 1 0 'Zak CummingsTrevor Smith'
 'Trevor SmithZak Cummings']
[10275]
['Trevor Smith' 'Zak Cummings' 185.0 75.0 'Orthodox' 3.29 55 3.31 51 1.7
 32 60 0.7 13858 37.0 'loss' 75 1 0 0 'Trevor SmithZak Cummings'
 'Zak CummingsTrevor Smith']
['Zak Cummings' 'Omari Akhmedov' 185.0 75.0 'Southpaw' 2.58 32 2.83 55
 0.68 28 65 0.7 12819 35.0 'loss' 72 0 1 0 'Zak CummingsOmari Akhmedov'
 'Omari AkhmedovZak Cummings']
[7983]
['Omari Akhmedov' 'Zak Cummings' 185.0 73.0 'Orthodox' 2.95 35 2.59 57
 2.63 49 65 0.3 11653 31.0 'win' 72 1 0 0 'Omari AkhmedovZak Cum

['Zhang Weili' 'Joanna Jedrzejczyk' 115.0 63.0 'Switch' 6.36 45 4.42 53
 1.24 23 100 0.5 11164 30.0 'win' 64 0 0 1 'Zhang WeiliJoanna Jedrzejczyk'
 'Joanna JedrzejczykZhang Weili']
[4948]
['Joanna Jedrzejczyk' 'Zhang Weili' 115.0 65.0 'Orthodox' 6.3 48 3.08 64
 0.28 62 81 0.1 11890 32.0 'loss' 66 1 0 0 'Joanna JedrzejczykZhang Weili'
 'Zhang WeiliJoanna Jedrzejczyk']
['Zhang Weili' 'Rose Namajunas' 115.0 63.0 'Switch' 6.36 45 4.42 53 1.24
 23 100 0.5 11577 31.0 'loss' 64 0 0 1 'Zhang WeiliRose Namajunas'
 'Rose NamajunasZhang Weili']
[8968]
['Rose Namajunas' 'Zhang Weili' 115.0 65.0 'Orthodox' 4.13 40 3.99 60 1.89
 53 50 0.8 10526 28.0 'win' 65 1 0 0 'Rose NamajunasZhang Weili'
 'Zhang WeiliRose Namajunas']
['Zhang Weili' 'Jessica Andrade' 115.0 63.0 'Switch' 6.36 45 4.42 53 1.24
 23 100 0.5 10975 30.0 'win' 64 0 0 1 'Zhang WeiliJessica Andrade'
 'Jessica AndradeZhang Weili']
[4800]
['Jessica Andrade' 'Zhang Weili' 115.0 62.0 'Orthodox' 6.15 50 5.2 52 2.97
 55 66 0.4 10202 27.0 'loss' 

In [56]:
final_df.head()

fighter1       fighter2  weight_f1  reach_f1 stance_f1  slpm_f1  \
0      Aalon Cruz     Uros Medic      145.0      78.0    Switch     7.58   
1      Aalon Cruz  Spike Carlyle      145.0      78.0    Switch     7.58   
2  Aaron Phillips     Matt Hobar      135.0      71.0  Southpaw     1.65   
3  Aaron Phillips     Jack Shore      135.0      71.0  Southpaw     1.65   
4  Aaron Phillips    Sam Sicilia      135.0      71.0  Southpaw     1.65   

  stracc_f1  sapm_f1 strdef_f1  tdavg_f1 tdacc_f1 tddef_f1  subavg_f1  \
0        39     8.88        58       0.0        0        0        0.0   
1        39     8.88        58       0.0        0        0        0.0   
2        56     3.44        39       0.0        0       44        0.4   
3        56     3.44        39       0.0        0       44        0.4   
4        56     3.44        39       0.0        0       44        0.4   

  age_days_f1  age_f1 outcome_f1 height_in_f1 stance_Orthodox_f1  \
0       11490    31.0       loss           72                  0   
1       11119    30.0       loss           72                  0   
2        9149    25.0       loss           69                  0   
3       11302    30.0       loss           69                  0   
4        9058    24.0       loss           69                  0   

  stance_Southpaw_f1 stance_Switch_f1                     concat  \
0                  0                1       Aalon CruzUros Medic   
1                  0                1    Aalon CruzSpike Carlyle   
2                  1                0   Aaron PhillipsMatt Hobar   
3                  1                0   Aaron PhillipsJack Shore   
4                  1                0  Aaron PhillipsSam Sicilia   

                     reverse       fighter1        fighter2  weight_f2  \
0       Uros MedicAalon Cruz     Uros Medic      Aalon Cruz      155.0   
1    Spike CarlyleAalon Cruz  Spike Carlyle      Aalon Cruz      145.0   
2   Matt HobarAaron Phillips     Matt Hobar  Aaron Phillips      135.0   
3   Jack ShoreAaron Phillips     Jack Shore  Aaron Phillips      135.0   
4  Sam SiciliaAaron Phillips    Sam Sicilia  Aaron Phillips      145.0   

   reach_f2 stance_f2  slpm_f2 stracc_f2  sapm_f2 strdef_f2  tdavg_f2  \
0      71.0  Southpaw    19.91        77     0.52        86      0.00   
1      71.0    Switch     2.55        54     3.85        30      3.34   
2      70.0  Southpaw     3.23        42     4.27        52      3.66   
3      71.0  Orthodox     3.14        57     1.61        56      5.52   
4      67.0  Orthodox     2.46        33     3.55        59      1.45   

  tdacc_f2 tddef_f2  subavg_f2 age_days_f2  age_f2 outcome_f2 height_in_f2  \
0        0      100        0.0       10177    27.0        win           73   
1       36       57        0.5        9795    26.0        win           68   
2       44       50        0.0       10090    27.0        win           70   
3       46      100        0.8        9291    25.0        win           68   
4       43       70        0.9       10339    28.0        win           68   

  stance_Orthodox_f2 stance_Southpaw_f2 stance_Switch_f2  \
0                  0                  1                0   
1                  0                  0                1   
2                  0                  1                0   
3                  1                  0                0   
4                  1                  0                0   

                     concat2                   reverse2  
0       Uros MedicAalon Cruz       Aalon CruzUros Medic  
1    Spike CarlyleAalon Cruz    Aalon CruzSpike Carlyle  
2   Matt HobarAaron Phillips   Aaron PhillipsMatt Hobar  
3   Jack ShoreAaron Phillips   Aaron PhillipsJack Shore  
4  Sam SiciliaAaron Phillips  Aaron PhillipsSam Sicilia

Note that in this final df any bouts with a missing fighter were

In [57]:
# fighter_stats[(fighter_stats.fighter == 'Aaron Riley') & (fighter_stats.opponent == 'Shane Nelson')]

In [58]:
# fighter_stats.iloc[0]

In [59]:
# fighter_stats.iloc[10360]

In [61]:
# test = np.concatenate((fighter_stats.iloc[0], fighter_stats.iloc[10360]))

In [62]:
# test